In [122]:
# Import libraries
import requests
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from IPython.display import display

In [84]:
# URL Link construction
country_url = "https://corona-api.com/countries"

In [85]:
# API call
raw_countries = requests.request("GET", country_url)
raw_countries = raw_countries.json()

In [86]:
# Transform data into pandas dataframe
df_countries = pd.DataFrame(raw_countries['data'])

In [87]:
# Get the uniques countries code for API iteration
country_code = list(df_countries.code.unique())

In [88]:
country_endpoint = []
for i in country_code:
    url = 'https://corona-api.com/countries/' + i
    country_endpoint.append(url)

In [89]:
def api_call(url):
    resp = requests.request("GET", url)
    resp = resp.json()
    return resp['data']

In [90]:
endpoint_response = {}
mylist = []

In [91]:
from concurrent.futures import ThreadPoolExecutor, as_completed

def download_file(url):
    try:
        resp = requests.get(url)
        resp_json = resp.json()
        mylist.append(resp_json['data'])
        return resp.status_code
    except requests.exceptions.RequestException as e:
       return e

def runner():
    threads= []
    with ThreadPoolExecutor(max_workers=20) as executor:
        for url in country_endpoint:
            threads.append(executor.submit(download_file, url))

runner()

In [92]:
endpoint_response = {'data': mylist}

In [93]:
df_country = pd.DataFrame(endpoint_response['data'])

In [94]:
#Create function to unpack arrays in timeline fields
def using_repeat(df):
    lens = [len(item) for item in df['timeline']]
    return pd.DataFrame( {"name" : np.repeat(df['name'].values,lens),
                          "coordinates" : np.repeat(df['coordinates'].values,lens),
                          "code" : np.repeat(df['code'].values,lens),
                          "population": np.repeat(df['population'].values,lens),
                          "timeline" : np.concatenate(df['timeline'].values)})

In [95]:
df_country = using_repeat(df_country)
df_country = df_country.join(pd.json_normalize(df_country["timeline"].tolist()).add_prefix("timeline.")).drop(["timeline"], axis=1)
df_country = df_country.join(pd.json_normalize(df_country["coordinates"].tolist()).add_prefix("coordinates.")).drop(["coordinates"], axis=1)

In [119]:
buttons=[]
country_list = list(df_country['name'].unique())
for col in country_list:
    buttons.append(dict(method='update',
                        label=col,
                        args=[{'y': df_country['timeline.confirmed'][df_country['name']==col]}])
                  )

In [118]:
buttons[0]

{'method': 'update',
 'label': 'Albania',
 'args': [{'y': 0      5396
   1      5105
   2      4997
   3      4880
   4      4763
          ... 
   139      33
   140      23
   141      12
   142      10
   143       2
   Name: timeline.confirmed, Length: 144, dtype: int64}]}

In [120]:
updatemenu=[]
your_menu=dict()
updatemenu.append(your_menu)
updatemenu[0]['buttons']=buttons
updatemenu[0]['direction']='down'
updatemenu[0]['showactive']=True

In [123]:
# Initialize figure
fig = go.Figure()

# Add traces
fig.add_trace(go.Scatter(x=df_country['timeline.date'], 
                         y=df_country['timeline.deaths'],
                         mode='markers',
                         name='deaths'))
    
fig.add_trace(go.Scatter(x=df_country['timeline.date'], 
                         y=df_country['timeline.active'],
                         mode='lines+markers',
                         name='active'))
    
fig.add_trace(go.Scatter(x=df_country['timeline.date'], 
                         y=df_country['timeline.recovered'],
                         mode='lines',
                         name='recovered'))

# update layout and show figure
fig.update_layout(updatemenus=updatemenu)
fig.show()

In [21]:
pd.to_datetime(df_country['timeline.date'])

0       2020-08-01
1       2020-07-29
2       2020-07-28
3       2020-07-27
4       2020-07-26
           ...    
26180   2020-03-24
26181   2020-03-23
26182   2020-03-22
26183   2020-03-19
26184   2020-03-18
Name: timeline.date, Length: 26185, dtype: datetime64[ns]

In [28]:
df_country.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26185 entries, 0 to 26184
Data columns (total 15 columns):
 #   Column                   Non-Null Count  Dtype  
---  ------                   --------------  -----  
 0   name                     26185 non-null  object 
 1   code                     26185 non-null  object 
 2   population               26185 non-null  float64
 3   timeline.updated_at      26185 non-null  object 
 4   timeline.date            26185 non-null  object 
 5   timeline.deaths          26185 non-null  int64  
 6   timeline.confirmed       26185 non-null  int64  
 7   timeline.active          26185 non-null  int64  
 8   timeline.recovered       26185 non-null  int64  
 9   timeline.new_confirmed   26185 non-null  int64  
 10  timeline.new_recovered   26185 non-null  int64  
 11  timeline.new_deaths      26185 non-null  int64  
 12  timeline.is_in_progress  192 non-null    object 
 13  coordinates.latitude     26185 non-null  float64
 14  coordinates.longitude 

In [39]:
df_long=pd.melt(df_country, 
                id_vars=['timeline.date', 'name'], 
                value_vars=['timeline.deaths', 'timeline.confirmed', 'timeline.recovered'])

In [41]:
df_long[df_long['name']=='Argentina']

timeline.date       name            variable  value
438      2020-08-01  Argentina     timeline.deaths   3558
439      2020-07-29  Argentina     timeline.deaths   3288
440      2020-07-28  Argentina     timeline.deaths   3179
441      2020-07-27  Argentina     timeline.deaths   3059
442      2020-07-26  Argentina     timeline.deaths   2939
...             ...        ...                 ...    ...
52950    2020-03-08  Argentina  timeline.recovered      0
52951    2020-03-07  Argentina  timeline.recovered      0
52952    2020-03-06  Argentina  timeline.recovered      0
52953    2020-03-04  Argentina  timeline.recovered      0
52954    2020-03-03  Argentina  timeline.recovered      0

[441 rows x 4 columns]

In [45]:
df_country['timeline.date']=pd.to_datetime(df_country['timeline.date'])

In [48]:
df_country.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 26185 entries, 0 to 26184
Data columns (total 15 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   name                     26185 non-null  object        
 1   code                     26185 non-null  object        
 2   population               26185 non-null  float64       
 3   timeline.updated_at      26185 non-null  object        
 4   timeline.date            26185 non-null  datetime64[ns]
 5   timeline.deaths          26185 non-null  int64         
 6   timeline.confirmed       26185 non-null  int64         
 7   timeline.active          26185 non-null  int64         
 8   timeline.recovered       26185 non-null  int64         
 9   timeline.new_confirmed   26185 non-null  int64         
 10  timeline.new_recovered   26185 non-null  int64         
 11  timeline.new_deaths      26185 non-null  int64         
 12  timeline.is_in_progress  192 non

In [51]:
df_country.groupby('timeline.date')["timeline.deaths"].sum()

timeline.date
2020-01-21        17
2020-01-22        35
2020-01-23        44
2020-01-24        68
2020-01-25        98
               ...  
2020-07-26    648371
2020-07-27    653771
2020-07-28    659330
2020-07-29    666714
2020-08-01    685151
Name: timeline.deaths, Length: 192, dtype: int64

In [78]:
tmp = pd.DataFrame(df_country.groupby('timeline.date').agg({'timeline.deaths': 'sum',
                                         'timeline.confirmed': 'sum',
                                        'timeline.recovered': 'sum'}))

In [81]:
tmp.head(n=100)

timeline.deaths  timeline.confirmed  timeline.recovered
timeline.date                                                         
2020-01-21                  17                 555                  28
2020-01-22                  35                1208                  58
2020-01-23                  44                1594                  66
2020-01-24                  68                2379                  75
2020-01-25                  98                3556                  91
...                        ...                 ...                 ...
2020-04-25              202812             2895027              815845
2020-04-26              206510             2969756              864902
2020-04-27              211133             3040045              893130
2020-04-28              217119             3114674              927833
2020-04-29              227603             3192161              971883

[100 rows x 3 columns]